In [7]:
import numpy as np
from scipy.optimize import curve_fit
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import matplotlib

def lorentzian(x, A, x0, gamma, k, b):
    return A / (1 + ((x - x0) / gamma)**2) + k * x + b
def double_lorentzian(x, A1, x1, gamma1, A2, x2, gamma2, k, b):
    return lorentzian(x, A1, x1, gamma1, k, b) + lorentzian(x, A2, x2, gamma2, 0, 0)
def triple_lorentzian(x, A1, x1, gamma1, A2, x2, gamma2, A3, x3, gamma3, k, b):
    return lorentzian(x, A1, x1, gamma1, k, b) + lorentzian(x, A2, x2, gamma2, 0, 0) + lorentzian(x, A3, x3, gamma3, 0, 0)
%pwd

'/home/chn/repo/SiC-2nd-paper'

In [8]:
def fitting_peek(x, y, x_range, function, guess, bound):
  mask = (x > x_range[0]) & (x < x_range[1])
  x = x[mask]
  y = y[mask]
  popt, pcov = curve_fit(function, x, y, p0=guess, maxfev=10000, bounds=bound)
  return popt

In [9]:
fitting_init_parameter = [
  [300, 196, 1, 2e3, 204, 0.8, 0, 900],
  [50, 266, 5, 0, 100],
  [1e3, 611, 5, 0, 100],
  [1e4, 776, 1, 1e3, 797, 1, 1, 100],
  [1e4, 776, 1, 1e4, 782, 1, 1e3, 797, 1, 1, 100],
  [1e4, 776, 1, 1, 100]
]
fitting_range = [
  [180, 220],
  [250, 280],
  [600, 617],
  [700, 850],
  [700, 850],
  [769, 783]
]
fitting_bound = [
  ([0, 192, 0, 0, 200, 0, -np.inf, -np.inf], [np.inf, 198, np.inf, np.inf, 206, np.inf, np.inf, np.inf]),
  ([0, 260, 0, -np.inf, -np.inf], [np.inf, 270, np.inf, np.inf, np.inf]),
  ([0, 605, 0, -np.inf, -np.inf], [np.inf, 617, np.inf, np.inf, np.inf]),
  (-np.inf, np.inf),
  (-np.inf, np.inf),
  (-np.inf, np.inf)
]

In [10]:
polarizations = [ "zyyz", "xyyx" ]
x = {p: [[None for h in range(2)] for s in range(10)] for p in polarizations}
y = {p: [[None for h in range(2)] for s in range(10)] for p in polarizations}
for h, h_name in enumerate([ "前", "后" ]):
  with open(f'画图/拉曼结果拟合/250923/1/{h_name}半.txt', 'r') as f:
    lines = f.readlines()
    for s in range(10):
      x["zyyz"][s][h] = np.array([float(i) for i in lines[0].strip().split()])
      y["zyyz"][s][h] = np.array([float(i) for i in lines[s+1].strip().split()[1:]])
for s in range(10):
  for h, h_name in enumerate([ "前", "后" ]):
    with open(f'画图/拉曼结果拟合/250923/2/{s+1}{h_name}半.txt', 'r') as f:
      data = np.loadtxt(f)
      x["xyyx"][s][h] = data[:,0]
      y["xyyx"][s][h] = data[:,1]
fig = go.Figure()
for p in polarizations:
  for s in range(10):
    for h in range(2):
      fig.add_trace(go.Scatter(x=x[p][s][h], y=y[p][s][h], mode='lines', name=f'{p} {s} {h}'))
fig.update_layout(width=1920, height=1080)
fig.show()

In [11]:
A11_shift = {p: [[None for h in range(2)] for s in range(10)] for p in polarizations}
for p in polarizations:
  for s in range(10):
    for h in range(2):
      popt = fitting_peek(np.array(x[p][s][h]), np.array(y[p][s][h]), fitting_range[2], lorentzian, fitting_init_parameter[2], fitting_bound[2])
      A11_shift[p][s][h] = popt[1]
      print(f'{p} {s} {h} {A11_shift[p][s][h]}')
      if A11_shift[p][s][h] < 608 or A11_shift[p][s][h] > 610:
        print(error)
E23_shift = {p: [None for s in range(10)] for p in polarizations}
for p in [ "zyyz" ]:
  for s in range(10):
    popt = fitting_peek(np.array(x[p][s][1]), np.array(y[p][s][1]), fitting_range[3], double_lorentzian, fitting_init_parameter[3], fitting_bound[3])
    E23_shift[p][s] = popt[1]
    print(f'{p} {s} {E23_shift[p][s]}')
    if E23_shift[p][s] < 775 or E23_shift[p][s] > 777:
      print(error)
for p in [ "xyyx" ]:
  for s in range(10):
    popt = fitting_peek(np.array(x[p][s][1]), np.array(y[p][s][1]), fitting_range[4], triple_lorentzian, fitting_init_parameter[4], fitting_bound[4])
    E23_shift[p][s] = popt[1]
    print(f'{p} {s} {E23_shift[p][s]}')
    if E23_shift[p][s] < 775 or E23_shift[p][s] > 777:
      print(error)

zyyz 0 0 609.7769264446152
zyyz 0 1 609.8425124287717
zyyz 1 0 609.7879349007401
zyyz 1 1 609.8725594333473
zyyz 2 0 609.7923067476482
zyyz 2 1 609.9152330217634
zyyz 3 0 609.7900467664512
zyyz 3 1 609.9192260395312
zyyz 4 0 609.790298067011
zyyz 4 1 609.9031612580816
zyyz 5 0 609.7951338864971
zyyz 5 1 609.9271503699507
zyyz 6 0 609.7902776761968
zyyz 6 1 609.9179188741397
zyyz 7 0 609.7837627158226
zyyz 7 1 609.9386243422217
zyyz 8 0 609.8043861594849
zyyz 8 1 609.9430572359531
zyyz 9 0 609.7722187961788
zyyz 9 1 609.8984660899182
xyyx 0 0 609.3560499967953
xyyx 0 1 609.3941039878403
xyyx 1 0 609.3126333798893
xyyx 1 1 609.3219080454271
xyyx 2 0 609.2822318138416
xyyx 2 1 609.2840299432406
xyyx 3 0 609.2919046207884
xyyx 3 1 609.2265014328693
xyyx 4 0 609.3963803234666
xyyx 4 1 609.23494096793
xyyx 5 0 609.0824590602223
xyyx 5 1 609.1610090035532
xyyx 6 0 609.0126554211807
xyyx 6 1 609.1833015514956
xyyx 7 0 608.8800872445057
xyyx 7 1 608.9021817201975
xyyx 8 0 608.8207234582813
xyyx

In [12]:
# 将 E2-3 对齐到 776.5，将前半段使用 A1-1 的位移进行平移
x_combined = {p: [None for s in range(10)] for p in polarizations}
y_combined = {p: [None for s in range(10)] for p in polarizations}
for p in polarizations:
  for s in range(10):
    x_combined[p][s] = np.concatenate(((x[p][s][0] - A11_shift[p][s][0] + A11_shift[p][s][1] - E23_shift[p][s] + 776.5)[:852], x[p][s][1] - E23_shift[p][s] + 776.5))
    y_combined[p][s] = np.concatenate((y[p][s][0][:852], y[p][s][1]))
for p in polarizations:
  np.savetxt(f'画图/拉曼结果拟合/combined/substrate/{p}_x.txt', x_combined[p], fmt='%.6f')
  np.savetxt(f'画图/拉曼结果拟合/combined/substrate/{p}_y.txt', y_combined[p], fmt='%.6f')